In [1]:
import selenium
import pandas as pd
import numpy as np
from bs4 import BeautifulSoup
from time import sleep
from datetime import datetime

import selenium
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.common.action_chains import ActionChains
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.by import By
from selenium.common.exceptions import NoSuchElementException

import requests
import numpy as np

In [2]:
headers = {
    'User-Agent': 'Anselme F.E. Borgeaud (aborgeaud@gmail.com)'
}

In [3]:
driver = webdriver.Chrome()

In [4]:
driver.get('https://www.sec.gov/edgar/browse/?CIK=1050122')
# driver.get('https://www.sec.gov/edgar/browse/?CIK=1074078')
# driver.get('https://www.sec.gov/edgar/browse/?CIK=1923')

In [5]:
driver.title

'EDGAR Entity Landing Page'

In [9]:
search_elem = driver.find_element_by_xpath('//input[@placeholder="Search table"]')
search_elem.send_keys('10-K')

In [12]:
link_elem = driver.find_elements_by_class_name("document-link")

In [14]:
annual_report_elem = [e for e in link_elem if 'Annual report' in e.text]

In [17]:
for a in annual_report_elem:
    print(a.text)

Annual report [Section 13 and 15(d), not S-K Item 405]
Annual report [Section 13 and 15(d), not S-K Item 405]
Annual report [Section 13 and 15(d), not S-K Item 405]
Annual report [Section 13 and 15(d), not S-K Item 405]
Annual report [Section 13 and 15(d), not S-K Item 405]
Annual report [Section 13 and 15(d), not S-K Item 405]
Annual report [Section 13 and 15(d), not S-K Item 405]
Annual report [Section 13 and 15(d), not S-K Item 405]
Annual report [Section 13 and 15(d), not S-K Item 405]


In [14]:
report = annual_report_elem[0]
resp = requests.get(report.get_property('href'), headers=headers)

In [15]:
for a in annual_report_elem:
    print(a.get_property('href'))

https://www.sec.gov/Archives/edgar/data/0001050122/000110465907019474/a07-5825_110k.htm
https://www.sec.gov/Archives/edgar/data/0001050122/000110465906017311/a06-2743_110k.htm
https://www.sec.gov/Archives/edgar/data/0001050122/000104746905006925/a2153844z10-k.htm
https://www.sec.gov/Archives/edgar/data/0001050122/000110465904007882/a04-3568_110k.htm


In [10]:
soup = BeautifulSoup(resp.content)

In [115]:
soup

<html><body><document>
<type>10-K
<sequence>1
<filename>a07-5825_110k.htm
<description>10-K
<text>
<div style="font-family:Times New Roman;">
<div style="border:none;border-top:double windowtext 6.0pt;padding:0pt 0pt 0pt 0pt;"> <p style="border:none;margin:0pt 0pt .0001pt;padding:0pt;"><a name="scotch"></a><font face="Times New Roman" size="2" style="font-size:10.0pt;"> </font></p> </div>
<p style="font-weight:bold;margin:0pt 0pt .0001pt;page-break-after:avoid;text-align:center;"><b><font face="Times New Roman" size="5" style="font-size:16.5pt;">UNITED STATES</font></b></p>
<p style="font-weight:bold;margin:0pt 0pt .0001pt;page-break-after:avoid;text-align:center;"><b><font face="Times New Roman" size="5" style="font-size:16.5pt;">SECURITIES AND EXCHANGE
COMMISSION</font></b></p>
<p style="font-weight:bold;margin:0pt 0pt 3.0pt;page-break-after:avoid;text-align:center;"><b><font face="Times New Roman" size="1" style="font-size:8.5pt;">Washington,
D.C. 20549</font></b></p>
<p style="font

In [50]:
soup

<html><body><document>
<type>10-K
<sequence>1
<filename>d10k.htm
<description>FORM 10-K
<text>
<title>Form 10-K</title>
<hr align="left" color="#000000" noshade="" size="3"/> <p style="margin-top:0px;margin-bottom:0px"><font size="1"> </font></p> <p align="center" style="margin-top:0px;margin-bottom:0px"><font face="Times New Roman" size="4"><b>UNITED STATES </b></font></p> <p align="center" style="margin-top:0px;margin-bottom:0px"><font face="Times New Roman" size="4"><b>SECURITIES AND EXCHANGE COMMISSION </b></font></p> <p align="center" style="margin-top:0px;margin-bottom:0px"><font face="Times New Roman" size="3"><b>Washington, DC 20549 </b></font></p> <p style="margin-top:0px;margin-bottom:0px"><font size="1"> </font></p> <p align="center" style="margin-top:0px;margin-bottom:0px"><font face="Times New Roman" size="5"><b>FORM 10-K </b></font></p> <p style="margin-top:0px;margin-bottom:-6px"><font size="1"> </font></p> <p style="margin-top:0px;margin-bottom:0px"><font face="Times Ne

In [21]:
import re
from datetime import datetime

# ps = soup.findAll('p', {'align': 'center'})
# text = [p.get_text(strip=True).replace(u'\xa0', u' ') for p in ps if 'year ended' in p.text][0]

def get_date(soup):
    ps = soup.findAll("p")
    bs = soup.findAll("b")
    texts = [
        p.get_text(strip=True).replace(u"\xa0", u" ")
        for p in ps + bs
        if "year ended" in p.text
    ]
    if len(texts) > 0:
        match = re.findall(r"ended .*[0-9]{4}", texts[0])
        if len(match) == 1:
            date_str = match[0].replace("ended ", "")
            try:
                date = datetime.strptime(date_str, "%B %d, %Y")
                return date
            except:
                return None
        
get_date(soup)

datetime.datetime(2011, 4, 30, 0, 0)

In [72]:
index_balance = resp.text.find('Consolidated Balance Sheets')
index_cashflow = resp.text.find('Consolidated Statements of Cash Flows')

In [24]:
dfs = pd.read_html(resp.text[:])

In [25]:
len(dfs)

55

In [26]:
df_assets = []
df_current_liabilities = []
df_longterm_liabilities = []
df_equity = []
for df in dfs:
    try:
        if df[0].str.contains('Total assets').sum() > 0:
            df_assets.append(df)
        if df[0].str.contains(r'Total.*liabilities').sum() > 0:
            df_longterm_liabilities.append(df)
        if df[0].str.contains(r'Total.*liabilities').sum() > 0:
            df_current_liabilities.append(df)
        if df[0].str.contains(r"Total stockholder.*equity").sum() > 0:
            df_equity.append(df)
    except AttributeError:
        pass

In [76]:
df_assets[-3].tail()

0   1    2      3       4    5   6    7   \
21                         Goodwill NaN  NaN  35405   35405  NaN NaN  NaN   
22  Definite-lived intangibles, net NaN  NaN  13847   13847  NaN NaN  NaN   
23                            Other NaN  NaN   1357    1357  NaN NaN  NaN   
24               Total other assets NaN  NaN  51696   51696  NaN NaN  NaN   
25                     Total assets NaN  NaN      $  114945  NaN NaN  NaN   

       8       9    10  11  
21  22304   22304  NaN NaN  
22  11500   11500  NaN NaN  
23   1102    1102  NaN NaN  
24  35804   35804  NaN NaN  
25      $  100525  NaN NaN

In [27]:
print(len(df_assets))
print(len(df_longterm_liabilities))
print(len(df_current_liabilities))
print(len(df_equity))

4
1
1
1


In [29]:
df_equity = df_equity[-1]

In [31]:
df_equity.dropna(subset=[0], inplace=True)
df_equity.head()

0   1    2      3      4    5   \
2                         CURRENT  LIABILITIES: NaN  NaN    NaN    NaN  NaN   
3             Current portion of long-term debt NaN  NaN      $   1633  NaN   
4  Current portion of capital lease obligations NaN  NaN     58     58  NaN   
5                          Income taxes payable NaN  NaN    567    567  NaN   
6                              Accounts payable NaN  NaN  12063  12063  NaN   

   6    7      8      9    10  11  
2 NaN  NaN    NaN    NaN  NaN NaN  
3 NaN  NaN      $   2633  NaN NaN  
4 NaN  NaN     57     57  NaN NaN  
5 NaN  NaN    722    722  NaN NaN  
6 NaN  NaN  10821  10821  NaN NaN

In [35]:
def get_value(x):
    vals = [v for v in x.values if str(v) != 'nan']
    try:
        val = float(vals[-1]) * 1000
    except:
        return None
    return val

In [39]:
df_equity['val'] = df_equity.apply(lambda x: get_value(x), axis=1)
df_equity.head()

0   1    2      3      4    5  \
0                         CURRENT  LIABILITIES: NaN  NaN    NaN    NaN  NaN   
1             Current portion of long-term debt NaN  NaN      $   1633  NaN   
2  Current portion of capital lease obligations NaN  NaN     58     58  NaN   
3                          Income taxes payable NaN  NaN    567    567  NaN   
4                              Accounts payable NaN  NaN  12063  12063  NaN   

    6    7      8      9   10  11           val  
0 NaN  NaN    NaN    NaN  NaN NaN           NaN  
1 NaN  NaN      $   2633  NaN NaN  2.633000e+15  
2 NaN  NaN     57     57  NaN NaN  5.700000e+13  
3 NaN  NaN    722    722  NaN NaN  7.220000e+14  
4 NaN  NaN  10821  10821  NaN NaN  1.082100e+16

In [42]:
df_long_liab = df_equity[0]
df_long_liab.dropna(subset=[0], inplace=True)
vals = df_long_liab[df_long_liab[0].str.contains(r"Total.*liabilities")].values
vals

array([['Total liabilities', nan, nan, '301604', nan, nan, '311800', nan],
       ['Total liabilities and stockholders\x92 equity', nan, '$',
        '367839', nan, nan, '377714', nan]], dtype=object)

In [43]:
[v for v in vals[0] if str(v) != 'nan'][-1]

'311800'

In [12]:
df_long_liab.dropna(subset=[0])

NameError: name 'df_long_liab' is not defined